<a href="https://colab.research.google.com/github/arthijayaraman-lab/CREASE-2D/blob/main/CREASE%20Tutorials/Generate_3D_Structure_with_Ellipsoids.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
#@title Import statements
import os
import numpy as np
import pickle
import time
from scipy.special import erfcinv
from scipy.special import i0, i1
from scipy.interpolate import interp1d
import sys
import pandas as pd
import glob
import plotly.express as px
import matplotlib.pyplot as plt
import math
from scipy.spatial.transform import Rotation as R

In [2]:
#@title Computational Approach for Structure Generation of Anisotropic Particles (CASGAP) Codes

def casgap(params, restart, output):
    # Initialize random number generator
    np.random.seed(params['seed'])
    currentseed = np.random.default_rng()
    os.makedirs(restart['path'], exist_ok=True)
    os.makedirs(output['path'], exist_ok=True)

    if restart['flag']:
        with open(os.path.join(restart['path'], restart['file']), 'rb') as f:
            particlelist, loopstart, loopend = pickle.load(f)
        np.random.default_rng(currentseed)
    else:
        particlelist = phaseI(params)
        #particlelist['polyhedra'] = {'vertices': [], 'faces': {}, 'center': []}
        particlelist['polyhedra'] = {}
        particlelist['Nprime'] = 0
        particlelist['xyz'] = (np.random.rand(particlelist['N'], 3) - 0.5) * params['boxlength']
        loopstart = 1
        loopend = particlelist['N']
        currentseed = np.random.default_rng()
        with open(os.path.join(restart['path'], restart['file']), 'wb') as f:
            pickle.dump((particlelist, loopstart, loopend), f)

    start_time = time.time()
    for i in range(loopstart, loopend + 1):
        successflag, particlelist = phaseII(particlelist, params)
        if not successflag:
            break

        if i % restart['freq'] == 0:
            currentseed = np.random.default_rng()
            loopstart = i
            with open(os.path.join(restart['path'], restart['file']), 'wb') as f:
                pickle.dump((particlelist, loopstart, loopend), f)
            end_time1 = time.time()
            print(f"Writing Restart File! Current population is {i}. The time elapsed is {end_time1-start_time} seconds.")

        if i % output['freq'] == 0:
            write_data(output, particlelist, params)

    currentseed = np.random.default_rng()
    with open(os.path.join(restart['path'], restart['file']), 'wb') as f:
        pickle.dump((particlelist, loopstart, loopend), f)
    write_data(output, particlelist, params)

    partialvoli = 4 / 3 * np.pi * particlelist['ac'][:particlelist['Nprime'], 0] ** 2 * particlelist['ac'][
                                                                                        :particlelist['Nprime'], 1]
    actual_volfrac = np.sum(partialvoli) / params['boxlength'] ** 3
    end_time2 = time.time()
    if not successflag:
        print(
            f"Not all ellipsoids could be added. Final population is {particlelist['Nprime']}. Final volume fraction is {actual_volfrac}. The time elapsed is {end_time2 - start_time} seconds.")
    else:
        print(
            f"All ellipsoids were successfully added! Final population is {particlelist['Nprime']}. Final volume fraction is {actual_volfrac}. The time elapsed is {end_time2 - start_time} seconds.")

def check_overlap(particlelist, params):
    successflag = 0

    population = particlelist['Nprime']
    newind = population + 1
    ac = particlelist['ac'][newind - 1]
    q = particlelist['quat'][newind - 1]
    boundingradius = np.max(ac)
    newpolyhedra_unshifted = discretize_ellipsoid(ac, q, [0, 0, 0])

    maxattempts = 10000
    perturbfreq = 100  # resample new coords at this rate
    maxradii = np.max(particlelist['ac'][:population], axis=1)
    pos = particlelist['xyz'][:population]

    EPAclearance = 0.1
    for numattempts in range(1, maxattempts + 1):
        if numattempts % perturbfreq == 1:
            if numattempts < perturbfreq:
                coords = (np.random.rand(3) - 0.5) * params['boxlength']
            else:
                randvars = np.random.rand(3)
                zbins = np.linspace(-0.5 * params['boxlength'], 0.5 * params['boxlength'], 11)
                znum, _ = np.histogram(pos[:, 2], bins=zbins)
                maxznum = np.max(znum)
                minznum = np.min(znum)
                if maxznum == minznum:
                    zcoord = (randvars[0] - 0.5) * params['boxlength']
                else:
                    newznum = (maxznum - znum) / (maxznum - minznum)
                    cumznum = np.concatenate(([0],np.cumsum(newznum))) + np.arange(11) * 1e-10
                    cumznum /= cumznum[-1]
                    zcoord = np.interp(randvars[2], cumznum, zbins)
                zbinwidth = zbins[1] - zbins[0]
                zfilter = (pos[:, 2] > zcoord - zbinwidth / 2) & (pos[:, 2] <= zcoord + zbinwidth / 2)

                ybins = np.linspace(-0.5 * params['boxlength'], 0.5 * params['boxlength'], 11)
                ynum, _ = np.histogram(pos[zfilter, 1], bins=ybins)
                maxynum = np.max(ynum)
                minynum = np.min(ynum)
                if not np.sum(zfilter) or maxynum == minynum:
                    ycoord = (randvars[1] - 0.5) * params['boxlength']
                else:
                    newynum = (maxynum - ynum) / (maxynum - minynum)
                    cumynum = np.concatenate(([0],np.cumsum(newynum))) + np.arange(11) * 1e-10
                    cumynum /= cumynum[-1]
                    ycoord = np.interp(randvars[1], cumynum, ybins)
                ybinwidth = ybins[1] - ybins[0]
                yzfilter = zfilter & (pos[:, 1] > ycoord - ybinwidth / 2) & (pos[:, 1] <= ycoord + ybinwidth / 2)

                xbins = np.linspace(-0.5 * params['boxlength'], 0.5 * params['boxlength'], 11)
                xnum, _ = np.histogram(pos[yzfilter, 0], bins=xbins)
                maxxnum = np.max(xnum)
                minxnum = np.min(xnum)
                if not np.sum(yzfilter) or maxxnum == minxnum:
                    xcoord = (randvars[0] - 0.5) * params['boxlength']
                else:
                    newxnum = (maxxnum - xnum) / (maxxnum - minxnum)
                    cumxnum = np.concatenate(([0],np.cumsum(newxnum))) + np.arange(11) * 1e-10
                    cumxnum /= cumxnum[-1]
                    xcoord = np.interp(randvars[0], cumxnum, xbins)
                coords = np.array([xcoord, ycoord, zcoord])

        newpolyhedra = newpolyhedra_unshifted.copy()
        newpolyhedra['vertices'] = newpolyhedra['vertices'] + np.ones((newpolyhedra['vertices'].shape[0], 1)) * coords
        dist = np.sqrt(np.sum((np.ones((population, 1)) * coords - pos) ** 2, axis=1))
        potentialoverlap = (maxradii + boundingradius - dist > 0)

        if not np.any(potentialoverlap):
            successflag = 1
            break

        indices = np.where(potentialoverlap)[0]
        numintersections = 0
        cummulativeshift = np.array([0, 0, 0])
        for i in indices:
            #try:
            intersectionflag, intersectionsimplex = gjk_simplex(newpolyhedra, particlelist['polyhedra'][i])
            #except KeyError:
            #    continue

            if intersectionflag:
                numintersections += 1
                shiftvector, shiftdist = expandingpolytope_shift(newpolyhedra, particlelist['polyhedra'][i],
                                                                 intersectionsimplex)
                cummulativeshift = -shiftvector * (shiftdist + EPAclearance)

        if np.any(cummulativeshift):
            if not numattempts % 100:
                print(
                    f"Warning: Previous attempts failed to converge after {numattempts} attempts. Current ellipsoid has {numintersections} intersections. The population is {population}.")
            coords = coords + cummulativeshift
            coords = np.mod(coords + params['boxlength'] / 2, params['boxlength']) - params['boxlength'] / 2
        else:
            successflag = 1
            break

    return successflag, coords

def discretize_ellipsoid(axislengths, q, origin):
    # Find the axial vector from the quaternion
    axvec = np.array([
        [q[0]**2 + q[1]**2 - q[2]**2 - q[3]**2, 2*(q[1]*q[2] - q[0]*q[3]), 2*(q[1]*q[3] + q[0]*q[2])],
        [2*(q[1]*q[2] + q[0]*q[3]), q[0]**2 - q[1]**2 + q[2]**2 - q[3]**2, 2*(q[2]*q[3] - q[0]*q[1])],
        [2*(q[1]*q[3] - q[0]*q[2]), 2*(q[2]*q[3] + q[0]*q[1]), q[0]**2 - q[1]**2 - q[2]**2 + q[3]**2]
    ])
    mag_axvec = np.sqrt(axvec[0]**2 + axvec[1]**2 + axvec[2]**2)
    axvec = axvec / mag_axvec

    # Convert Ellipsoid to Polyhedron
    f = np.sqrt(2) - 1
    a, b, c = axislengths[0], axislengths[0], axislengths[1]
    X0 = a * np.array([1, f, f])
    Y0 = b * np.array([f, 1, f])
    Z0 = c * np.array([f, f, 1])
    allvertices = np.concatenate([
        np.column_stack((X0, Y0, Z0)),  # first octant: x y z
        np.column_stack((-X0, Y0, Z0)),  # second octant: -x y z
        np.column_stack((-X0, -Y0, Z0)),  # third octant: -x -y z
        np.column_stack((X0, -Y0, Z0)),  # fourth octant: x -y z
        np.column_stack((X0, Y0, -Z0)),  # fifth octant: x y -z
        np.column_stack((-X0, Y0, -Z0)),  # sixth octant: -x y -z
        np.column_stack((-X0, -Y0, -Z0)),  # seventh octant: -x -y -z
        np.column_stack((X0, -Y0, -Z0))  # eighth octant: x -y -z
    ])
    numvertices = allvertices.shape[0]
    allvertices = np.dot(allvertices, axvec.T) + np.ones((numvertices, 1)) * origin
    allfaces = [
        [1, 10, 22, 13],  # +x rect
        [4, 16, 19, 7],  # -x rect
        [2, 14, 17, 5],  # +y rect
        [8, 20, 23, 11],  # -y rect
        [3, 6, 9, 12],  # +z rect
        [15, 24, 21, 18],  # -z rect
        [1, 3, 12, 10],  # +x+z rect
        [4, 7, 9, 6],  # -x+z rect
        [16, 18, 21, 19],  # -x-z rect
        [13, 22, 24, 15],  # +x-z rect
        [2, 5, 6, 3],  # +y+z rect
        [8, 11, 12, 9],  # -y+z rect
        [20, 21, 24, 23],  # -y-z rect
        [14, 15, 18, 17],  # +y-z rect
        [1, 13, 14, 2],  # +x+y rect
        [4, 5, 17, 16],  # -x+y rect
        [7, 19, 20, 8],  # -x-y rect
        [10, 11, 23, 22],  # +x-y rect
        [1, 2, 3],  # +x+y+z tri
        [4, 6, 5],  # -x+y+z tri
        [7, 8, 9],  # -x-y+z tri
        [10, 12, 11],  # +x-y+z tri
        [13, 15, 14],  # +x+y-z tri
        [16, 17, 18],  # -x+y-z tri
        [19, 21, 20],  # -x-y-z tri
        [22, 23, 24]  # +x-y-z tri
    ]
    polyhedra = {
        'vertices': allvertices,
        'faces': allfaces,
        'center': origin
    }

    return polyhedra

def expandingpolytope_shift(polyhedron1, polyhedron2, simplex):
    polytope = {
        'vertices': simplex['vertices'],
        'faces': simplex['faces']
    }
    facenorms = getfacenormals(polytope)
    tolerance = 1e-6
    #counter=0
    while True:
        #counter += 1
        #print(f"I am stuck here. {counter}")
        minInd, mindist = findnearestface(polytope, facenorms)
        nearestnormal = facenorms[minInd]
        support = supportpoint(polyhedron1, polyhedron2, nearestnormal)[0]
        supportdist = np.dot(nearestnormal, support)
        if (supportdist - mindist) > tolerance:
            numnormals = facenorms.shape[0]
            uniqueedges = []
            newfaces = []
            newnormals = []
            for i in range(numnormals):
                face = polytope['faces'][i]
                facevertex1 = polytope['vertices'][face[0]-1]
                if np.dot(facenorms[i], support - facevertex1) > tolerance:
                    faceedges = np.column_stack((face[:-1], face[1:]))
                    faceedges = np.vstack((faceedges, [face[-1], face[0]]))
                    uniqueedges = finduniqueedges(uniqueedges, faceedges)
                else:
                    newfaces.append(polytope['faces'][i])
                    newnormals.append(facenorms[i])
            # add the new support point to the polytope
            polytope['vertices'] = np.vstack((polytope['vertices'], support))
            supportind = polytope['vertices'].shape[0]
            numuniqueedges = uniqueedges.shape[0]
            for i in range(numuniqueedges):
                newaddedface, newaddedfacenorm = createnewpolytopeface(polytope, uniqueedges[i], supportind)
                newfaces.append(newaddedface)
                newnormals.append(newaddedfacenorm)
            polytope['faces'] = newfaces
            facenorms = np.array(newnormals)
        else:
            shiftvector = nearestnormal
            shiftdist = mindist
            break

    return shiftvector, shiftdist

def getfacenormals(polytope):
    faces = polytope['faces']
    numfaces = len(faces)
    facenorms = np.zeros((numfaces, 3))
    tolerance = 1e-6
    for i in range(numfaces):
        face = faces[i]
        point_a = polytope['vertices'][face[0]-1]
        point_b = polytope['vertices'][face[1]-1]
        point_c = polytope['vertices'][face[2]-1]
        vec_ab = point_b - point_a
        vec_bc = point_c - point_b
        facenorm_abc = np.cross(vec_ab, vec_bc)
        facedist = np.dot(point_a, facenorm_abc)
        if facedist < tolerance:
            facenorm_abc = -facenorm_abc
        facenorms[i] = facenorm_abc / np.linalg.norm(facenorm_abc)  # These are unit vectors

    return facenorms


def finduniqueedges(uniqueedges, faceedges):
    if len(uniqueedges) == 0:
        uniqueedges = faceedges
    else:
        for i in range(faceedges.shape[0]):
            # check if the reverse of  uniqueedge is in the faceedge. If there is, then delete.
            uniqueedge_vert1 = uniqueedges[:, 0] - faceedges[i, 1]
            uniqueedge_vert2 = uniqueedges[:, 1] - faceedges[i, 0]
            uniqueness_check = np.logical_not(uniqueedge_vert1) & np.logical_not(uniqueedge_vert2)
            if np.any(uniqueness_check):
                uniqueedges = uniqueedges[np.logical_not(uniqueness_check), :]
            else:
                uniqueedges = np.vstack((uniqueedges, faceedges[i, :]))
    return uniqueedges


def createnewpolytopeface(polytope, edge, pointind):
    point_a = polytope['vertices'][edge[0]-1, :]
    point_b = polytope['vertices'][edge[1]-1, :]
    point_c = polytope['vertices'][pointind-1, :]
    tolerance = 1e-6
    vec_ab = point_b - point_a
    vec_bc = point_c - point_b
    facenorm_abc = np.cross(vec_ab, vec_bc)
    facenorm = facenorm_abc / np.linalg.norm(facenorm_abc)  # These are unit vectors
    facedist = np.dot(point_a, facenorm)
    if facedist > tolerance:
        face = [edge[0], edge[1], pointind]
    else:
        face = [edge[1], edge[0], pointind]
        facenorm = -facenorm
    return face, facenorm

def findnearestface(polytope, facenorms):
    #distances = np.dot(polytope['vertices'][x[0]-1 for x in polytope['faces']], facenorms.T)
    facevertex=np.array([polytope['vertices'][x[0]-1] for x in polytope['faces']])
    distances = np.einsum("ij,ij->i",facevertex,facenorms)
    minInd = np.argmin(distances)
    mindist = distances[minInd]
    return minInd, mindist

def gjk_simplex(polyhedron1, polyhedron2):
    direction = polyhedron1['center'] - polyhedron2['center']
    support = supportpoint(polyhedron1, polyhedron2, direction)[0]
    simplexvertices = support
    direction = -np.array(support)

    while True:
        support = supportpoint(polyhedron1, polyhedron2, direction)[0]

        if np.all(np.logical_not(direction)) or np.dot(support, direction) <= 0:
            intersection_flag = 0
            simplex = {'vertices': []}
            break

        simplexvertices = np.vstack((support, simplexvertices))
        flag, simplexvertices, direction = nextsimplex(simplexvertices)

        if flag:
            if simplexvertices.shape[0] < 4:
                intersection_flag = 0
                simplex = {'vertices': []}
            else:
                intersection_flag = 1
                simplexfaces = gettetrahedronfaces(simplexvertices, [0, 0, 0])
                simplex = {'vertices': simplexvertices, 'faces': simplexfaces}
            break

    return intersection_flag, simplex


def nextsimplex(vertices):
    num_vertices = len(vertices)
    if num_vertices == 2:
        flag, vertices, direction = linesimplex(vertices)
    elif num_vertices == 3:
        flag, vertices, direction = trianglesimplex(vertices)
    elif num_vertices == 4:
        flag, vertices, direction = tetrahedronsimplex(vertices)
    else:
        flag = False
        vertices = []
        direction = np.array([])

    return flag, vertices, direction

def linesimplex(vertices):
    direction = np.zeros(3)
    point_a = vertices[0]
    point_b = vertices[1]
    vec_ab = point_b - point_a
    vec_ao = -point_a
    norm_abo = np.cross(vec_ab, vec_ao)

    if np.linalg.norm(norm_abo):  # check for collinearity
        direction = np.cross(norm_abo, vec_ab)
        flag = False
    else:
        flag = True

    return flag, vertices, direction

def trianglesimplex(vertices):
    direction = np.zeros(3)
    point_a = vertices[0]
    point_b = vertices[1]
    point_c = vertices[2]

    vec_ab = point_b - point_a
    vec_ac = point_c - point_a
    vec_ao = -point_a

    facenorm_abc = np.cross(vec_ab, vec_ac)

    if np.linalg.norm(facenorm_abc):  # check if origin is coplanar
        if np.dot(facenorm_abc, vec_ao) > 0:
            direction = facenorm_abc
            flag = False
        else:
            direction = -facenorm_abc
            flag = False
    else:
        flag = True

    return flag, vertices, direction

def tetrahedronsimplex(vertices):
    direction = np.zeros(3)
    point_a = vertices[0]
    point_b = vertices[1]
    point_c = vertices[2]
    point_d = vertices[3]

    vec_ab = point_b - point_a
    vec_ac = point_c - point_a
    vec_ad = point_d - point_a
    vec_ao = -point_a

    facenorm_abc = np.cross(vec_ab, vec_ac)
    if np.dot(facenorm_abc, vec_ad) > 0:
        facenorm_abc = -facenorm_abc

    facenorm_acd = np.cross(vec_ac, vec_ad)
    if np.dot(facenorm_acd, vec_ab) > 0:
        facenorm_acd = -facenorm_acd

    facenorm_abd = np.cross(vec_ab, vec_ad)
    if np.dot(facenorm_abd, vec_ac) > 0:
        facenorm_abd = -facenorm_abd

    outsideabc = np.dot(facenorm_abc, vec_ao) > 0
    outsideacd = np.dot(facenorm_acd, vec_ao) > 0
    outsideabd = np.dot(facenorm_abd, vec_ao) > 0

    if (outsideabc and outsideacd) or (outsideacd and outsideabd) or (outsideabd and outsideabc):
        flag = False
    elif outsideabc:
        vertices = np.array([point_a, point_b, point_c])
        direction = facenorm_abc
        flag = False
    elif outsideacd:
        vertices = np.array([point_a, point_c, point_d])
        direction = facenorm_acd
        flag = False
    elif outsideabd:
        vertices = np.array([point_a, point_b, point_d])
        direction = facenorm_abd
        flag = False
    else:
        flag = True

    return flag, vertices, direction


def gettetrahedronfaces(vertices, interiorpoint):
    if vertices.shape[0] != 4:
        raise ValueError('Input should be a set of tetrahedral vertices')

    faces = [[1, 2, 3], [1, 4, 2], [1, 3, 4], [2, 4, 3]]

    for i in range(4):
        face = faces[i]
        point_a = vertices[face[0] - 1]
        point_b = vertices[face[1] - 1]
        point_c = vertices[face[2] - 1]

        vec_ab = point_b - point_a
        vec_bc = point_c - point_b
        facenorm_abc = np.cross(vec_ab, vec_bc)

        if np.dot(facenorm_abc, point_b - interiorpoint) < 0:
            faces[i] = [face[0], face[2], face[1]]

    return faces

def phaseI(params):
    #np.random.seed()  # Reset the random seed

    target_volfrac = params['volfrac']
    box_vol = params['boxlength'] ** 3
    vol_prefactor = 4 / 3 * np.pi
    mean_vol = vol_prefactor * params['mean_R'] ** 3

    # Total number of particles
    N = round(2 * target_volfrac / mean_vol * box_vol)  # Factor of 2 is for good measure.

    # Parameters for lognormal distribution
    R_logmu = np.log(params['mean_R'] ** 2 / np.sqrt(params['mean_R'] ** 2 + params['sd_R'] ** 2))
    gamma_logmu = np.log(params['mean_gamma'] ** 2 / np.sqrt(params['mean_gamma'] ** 2 + params['sd_gamma'] ** 2))
    R_logsigma = np.sqrt(np.log(1 + params['sd_R'] ** 2 / params['mean_R'] ** 2))
    gamma_logsigma = np.sqrt(np.log(1 + params['sd_gamma'] ** 2 / params['mean_gamma'] ** 2))

    # Generate random samples of R
    Ri = lognormrandvar((N, 1), R_logmu, R_logsigma)
    partialvoli = vol_prefactor * Ri ** 3 / box_vol
    actual_volfrac = np.sum(partialvoli)

    while actual_volfrac <= target_volfrac:
        Ri_extra = lognormrandvar((N, 1), R_logmu, R_logsigma)
        Ri = np.concatenate((Ri, Ri_extra))
        voli_extra = vol_prefactor * Ri_extra ** 3 / box_vol
        partialvoli = np.concatenate((partialvoli, voli_extra))
        actual_volfrac = np.sum(partialvoli)

    if actual_volfrac > target_volfrac:
        N = np.argmax(np.cumsum(partialvoli) > target_volfrac)  # Find index where cumulative sum exceeds target_volfrac
        Ri = Ri[:N]

    # Generate random samples of gamma
    gammai = lognormrandvar((N, 1), gamma_logmu, gamma_logsigma)

    # Set spheroid axis lengths
    ai = Ri / gammai ** (1 / 3)
    ci = Ri * gammai ** (2 / 3)
    ac = np.hstack((ai, ci))
    Lambda = generate_quat(params['W'], params['omega'])
    quat = samplequat(N, Lambda, params['kappa'])

    particlelist = {'N': N, 'ac': ac, 'quat': quat}

    print(f"Phase I completed! N is {N}.")
    return particlelist


def lognormrandvar(size, logmu, logsigma):
    temp = -np.sqrt(2) * erfcinv(2 * np.random.rand(*size))  # Std normal random variable
    result = np.exp(logmu + temp * logsigma)
    return result


def generate_quat(W, omega):
    alpha_by_2 = omega / 2 * np.pi / 180  # Convert angle to radians
    norm = W / np.sqrt(np.sum(W** 2))
    q = np.array([np.cos(alpha_by_2),norm[0] * np.sin(alpha_by_2),norm[1] * np.sin(alpha_by_2),norm[2] * np.sin(alpha_by_2)])
    return q


def samplequat(num, pref_q, kappa):
    v = -np.sqrt(2) * erfcinv(2 * np.random.rand(num, 2))
    vsum = np.sqrt(np.sum(v ** 2, axis=1))
    v = v / vsum[:, np.newaxis]  # Ensure shape compatibility

    if kappa:
        randnum = np.random.rand(num)
        w = 1 + 1 / kappa * np.log(randnum + (1 - randnum) * np.exp(-2 * kappa))
    else:
        w = 2 * np.random.rand(num) - 1

    orgvec = np.hstack((np.zeros((num, 2)), np.ones((num, 1))))
    newvec = np.vstack((w, np.sqrt(1 - w ** 2) * v[:, 0], np.sqrt(1 - w ** 2) * v[:, 1])).T

    axisvec = np.cross(orgvec, newvec)
    axisvec /= np.sqrt(np.sum(axisvec ** 2, axis=1, keepdims=True))  # Ensure shape compatibility
    axistheta = np.arccos(np.sum(orgvec * newvec, axis=1))

    cos_half = np.cos(axistheta / 2)[:, np.newaxis]  # Reshape to (num, 1)
    sin_half = np.sin(axistheta / 2)[:, np.newaxis]  # Reshape to (num, 1)
    quats = np.hstack((cos_half, sin_half * axisvec))  # Concatenate along axis 1

    if kappa:
        Mumat = np.zeros((4, 4))
        Mumat[:, 0] = pref_q.T
        Q, R = np.linalg.qr(Mumat)
        if R[0, 0] < 0:
            Q = -Q
        result = np.dot(Q, quats.T).T
    else:
        result = quats

    return result

def phaseII(particlelist, params):
    if particlelist['Nprime']:
        # Check and adjust coords so that the new ellipsoid does not overlap
        # with any previous ellipsoids.
        successflag, coords = check_overlap(particlelist, params)
        if not successflag:
            return successflag, particlelist

        # Increment population
        population = particlelist['Nprime'] + 1
        particlelist['xyz'][population-1, :] = coords
    else:
        # It is the first particle, there can't be any overlap!
        successflag = 1
        population = 1
        coords = particlelist['xyz'][population-1, :]

    # Append polyhedra
    axislengths = particlelist['ac'][population-1, :]
    quats = particlelist['quat'][population-1, :]
    polyhedron = discretize_ellipsoid(axislengths, quats, coords)
    particlelist['polyhedra'][population-1] = polyhedron
    particlelist['Nprime'] = population
    return successflag, particlelist


def samplew(size, kappa):
    u = np.random.rand(size)
    w = np.arange(-1, 1, 0.0001)
    first_two_terms = 1 + (w * np.sqrt(1 - w**2) - np.arccos(w)) / np.pi
    mplus2_term = lambda m: (m + 1) / np.pi * (np.sin((m + 2) * np.arccos(w)) / (m + 2) - np.sin(m * np.arccos(w)) / m) * i1(m + 1, kappa) / i1(1, kappa)
    Fw = first_two_terms
    mvalue = 1
    if kappa:
        while True:
            newterm = mplus2_term(mvalue)
            newterm_magnitude = np.sqrt(np.sum(newterm**2))
            if np.isnan(newterm_magnitude):
                raise ValueError("Nan values detected, kappa is too high!")
            elif abs(newterm_magnitude) < 1e-10:
                break
            Fw += newterm
            mvalue += 1
    Fw[np.abs(Fw) < 1e-10] = 0
    if not np.all(np.diff(Fw) >= 0):
        raise ValueError("Cumulative function is not monotonic!")
    smallseries = np.linspace(0, 1e-15, len(w))
    data = np.column_stack((w, (Fw + smallseries) / (Fw[-1] + smallseries[-1])))
    sampledvalues = interp1d(data[:, 1], data[:, 0])(u)
    return sampledvalues


def supportpoint(polyhedron1, polyhedron2, direction):
    furthestpoint1 = furthestpoint(polyhedron1['vertices'], direction)
    furthestpoint2 = furthestpoint(polyhedron2['vertices'], -direction)
    point = furthestpoint1 - furthestpoint2
    return point, furthestpoint1, furthestpoint2


def furthestpoint(vertices, direction):
    maxpoint = np.zeros(3)
    maxprojection = -np.inf
    for i in range(vertices.shape[0]):
        projection = np.dot(vertices[i], direction)
        if maxprojection < projection:
            maxprojection = projection
            maxpoint = vertices[i]
    return maxpoint

def write_data(output, particlelist, params):
    population = particlelist['Nprime']
    fileID = open(output['path'] + output['file'], 'w')
    fileID.write('ITEM: TIMESTEP\n0\n')
    fileID.write('ITEM: NUMBER OF ATOMS\n%d\n' % population)
    fileID.write('ITEM: BOX BOUNDS pp pp pp\n%f %f\n%f %f\n%f %f\n' % (-params['boxlength']/2, params['boxlength']/2, -params['boxlength']/2, params['boxlength']/2, -params['boxlength']/2, params['boxlength']/2))
    fileID.write('ITEM: ATOMS id type x y z a b c qw qx qy qz\n')
    Alldata = [(i+1, particlelist['xyz'][i][0], particlelist['xyz'][i][1], particlelist['xyz'][i][2], particlelist['ac'][i][0], particlelist['ac'][i][0], particlelist['ac'][i][1], particlelist['quat'][i][0], particlelist['quat'][i][1], particlelist['quat'][i][2], particlelist['quat'][i][3]) for i in range(population)]
    for data in Alldata:
        fileID.write('%d 1 %f %f %f %f %f %f %f %f %f %f\n' % data)

    fileID.close()

In [6]:
#@title Choose your structural parameters to generate a 3D ellipsoidal particle structure
params = {
    "seed": 11351,                    # Random Seed
    "boxlength": 100,                 # Length of the box
    "mean_R": 10,                      # Mean of volumetric radii
    "sd_R": 0.1,                    # Standard Deviation of volumetric radii
    "mean_gamma": 2,                  # Mean of aspect ratio
    "sd_gamma": 0.1,                # Standard Deviation of aspect ratio
    "W": [-np.sqrt(6 + 3 * np.sqrt(3)), np.sqrt(2 + np.sqrt(3)), 0] / np.sqrt(8 + 4 * np.sqrt(3)),  # Orientation axis
    "omega": -75,                     # Orientation angle parameter
    "kappa": 100,                       # Orientation anisotropy parameter
    "volfrac": 0.1                    # Target volume fraction
}

restart = {
    "flag": 0,
    "path": './restart/',
    "file": 'session.txt',
    "freq": 1000
}

output = {
    "file": 'sample.dump',
    "path": './output/',
    "freq": 1000
}
casgap(params,restart,output)


Phase I completed! N is 23.
All ellipsoids were successfully added! Final population is 23. Final volume fraction is 0.09617175386252208. The time elapsed is 0.16495871543884277 seconds.


In [7]:
#@title Fill particles of casgap structure with scatterers
def quaternion_rotation_matrix(qw,qx,qy,qz):
    rot = R.from_quat([qx,qy,qz,qw])
    return rot.as_matrix()

def generate_points_monte_carlo_ellipsoid(a, b, c, density, rot_matrix, x_0, y_0, z_0):
    volume = (4/3) * np.pi * a * b * c
    num_points = int(density * volume)

    if num_points == 0:
        return np.empty((0,3), dtype=np.float32)

    # Acceptance probability ~ volume_of_ellipsoid / volume_of_bounding_box = ( (4/3)*pi*a*b*c ) / (8*a*b*c ) = pi/6 ~ 0.5236
    # We choose an overshoot factor so we likely get enough points in one go.

    overshoot_factor =2
    candidate_count = int(overshoot_factor * num_points)

    x = np.random.uniform(-a, a, candidate_count)
    y = np.random.uniform(-b, b, candidate_count)
    z = np.random.uniform(-c, c, candidate_count)

    mask = ((x**2)/a**2) + ((y**2) / b**2) + ((z**2) / c**2) <= 1
    filtered_points = np.vstack((x[mask], y[mask], z[mask])).T
    if filtered_points.shape[0] > num_points:
        filtered_points = filtered_points[:num_points]
    points = (filtered_points @ rot_matrix.T) + np.array([x_0, y_0, z_0], dtype=filtered_points.dtype)
    return points

def process_file(file_path, output_folder, base_density=1):
    with open(file_path, 'r') as f:
        box_len = [next(f) for _ in range(8)][-3:]
    # Read the particle data
    col_names = ['mol', 'type', 'x', 'y', 'z', 'a', 'b', 'c', 'qw', 'qx', 'qy', 'qz']

    total_points = 0
    df_iter = pd.read_csv(file_path, skiprows=9, header=None, sep='\s+', names=col_names, chunksize=1000)
    for chunk in df_iter:
        for _, row in chunk.iterrows():
            a, b, c = row[['a', 'b', 'c']].values
            volume = (4/3)*np.pi*a*b*c
            num_points = int(base_density*volume)
            total_points += num_points

    output_file = os.path.join(output_folder, os.path.basename(file_path).replace('.dump', '_scatterers.dump'))
    with open(output_file, 'w') as out_f:
        out_f.write("ITEM: TIMESTEP\n")
        out_f.write('0\n')
        out_f.write("ITEM: NUMBER OF ATOMS\n")
        out_f.write(str(total_points)+'\n')
        out_f.write("ITEM: BOX BOUNDS pp pp pp\n")
        out_f.write(''.join(box_len))
        out_f.write("ITEM: ATOMS id mol type x y z\n")

    current_id = 1
    df_iter = pd.read_csv(file_path, skiprows=9, header=None, sep='\s+', names=col_names, chunksize=1000)

    with open(output_file, 'a') as out_f:
        for chunk in df_iter:
            for _, row in chunk.iterrows():
                a, b, c = row[['a', 'b', 'c']].values
                x_0, y_0, z_0 = row[['x','y','z']].values
                qw, qx, qy, qz = row[['qw','qx','qy','qz']].values
                particle_id = row['mol']
                particle_type = row['type']

                rot_matrix = quaternion_rotation_matrix(qw, qx, qy, qz)
                points_ellipsoid = generate_points_monte_carlo_ellipsoid(a, b, c, base_density, rot_matrix, x_0, y_0, z_0)

                # Write points directly to file
                for p in points_ellipsoid:
                    out_f.write(f"{current_id} {particle_id} {particle_type} {p[0]} {p[1]} {p[2]}\n")
                    current_id += 1

    print(f"Scatterers file saved to {output_file}")

process_file('/content/output/sample.dump', 'output/')

Scatterers file saved to output/sample_scatterers.dump


In [8]:
#@title Visualize 3D structure with scatterers

input_file = '/content/output/sample_scatterers.dump'

# Initialize lists to hold the data
timestep = None
number_of_atoms = None
box_bounds = []
atoms_data = []

# Parse the LAMMPS dump file
with open(input_file, 'r') as file:
    lines = file.readlines()
    i = 0
    while i < len(lines):
        line = lines[i].strip()
        if "ITEM: TIMESTEP" in line:
            timestep = int(lines[i + 1].strip())
            i += 2
        elif "ITEM: NUMBER OF ATOMS" in line:
            number_of_atoms = int(lines[i + 1].strip())
            i += 2
        elif "ITEM: BOX BOUNDS" in line:
            box_bounds = [list(map(float, lines[i + j + 1].strip().split())) for j in range(3)]
            i += 4
        elif "ITEM: ATOMS" in line:
            headers = line.split()[2:]
            for j in range(number_of_atoms):
                atom_data = list(map(float, lines[i + j + 1].strip().split()))
                atoms_data.append(atom_data)
            i += number_of_atoms + 1
        else:
            i += 1

# Convert the parsed atom data to a DataFrame
columns = ['id', 'mol', 'type', 'x', 'y', 'z']
df = pd.DataFrame(atoms_data, columns=columns)

# Create a 3D scatter plot using Plotly
fig = px.scatter_3d(df, x='x', y='y', z='z', color='id',labels={'x': 'X Position', 'y': 'Y Position', 'z': 'Z Position'})
fig.update_traces(marker=dict(size=1))

# Show the plot in an interactive format for notebooks
fig.show()
